# Covid19 US Dashboard
![Coronavirus particle Image](https://www.apta.com/wp-content/uploads/home-banner-1.jpg)

In [1]:
# importing libraries

from __future__ import print_function
from ipywidgets import interact, interactive, fixed, interact_manual
from IPython.core.display import display, HTML

import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import plotly.express as px
import folium
import plotly.graph_objects as go
import seaborn as sns
import ipywidgets as widgets
import requests


In [2]:
# loading data right from the source:
death_df = pd.read_csv('https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_deaths_US.csv')
confirmed_df = pd.read_csv('https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_confirmed_US.csv')


In [3]:
confirmed_df.set_index(confirmed_df['Province_State'],inplace=True)
confirmed_df.rename(columns={'Province_State': 'State'},inplace=True)
death_df.set_index(death_df['Province_State'],inplace=True)
death_df.rename(columns={'Province_State': 'State'},inplace=True)

In [4]:
confirmed_df_states=confirmed_df.drop(columns=['UID', 'code3', 'FIPS', 'Lat', 'Long_']).groupby(['State']).sum().copy()
death_df_states=death_df.drop(columns=['UID', 'code3', 'FIPS', 'Lat', 'Long_']).groupby(['State']).sum().copy()

In [5]:
confirmed_df_states=pd.merge(confirmed_df[['Lat', 'Long_','State']].groupby(['State']).mean(),confirmed_df_states, left_index=True, right_index=True)
death_df_states=pd.merge(death_df[['Lat', 'Long_','State']].groupby(['State']).mean(),death_df_states, left_index=True, right_index=True)

In [6]:
combined_df=pd.DataFrame()
combined_df['Confirmed']=confirmed_df_states[confirmed_df_states.columns[-1]]
combined_df['Deaths']=death_df_states[death_df_states.columns[-1]]

### Statewise Data

In [7]:
sorted_combined_df=combined_df.loc[:,["Confirmed","Deaths"]].sort_values("Confirmed",ascending=False)
sorted_combined_df['State']=sorted_combined_df.index
combined_df.loc[:,["Confirmed","Deaths"]].sort_values("Confirmed",ascending=False).style.background_gradient(cmap='Blues',subset=["Confirmed"]).background_gradient(cmap='Reds',subset=["Deaths"])

### 10 worst hit States - Confirmed cases

In [8]:
px.bar(
    sorted_combined_df.head(10),
    x = "State",
    y = "Confirmed",
    title= "Top 10 worst affected States", # the axis names
    color_discrete_sequence=["Orange"], 
    height=500,
    width=800
)

### 10 worst hit States - Death cases

In [9]:
px.bar(
    sorted_combined_df.head(10),
    x = "State",
    y = "Deaths",
    title= "Top 10 worst affected States", # the axis names
    color_discrete_sequence=["red"], 
    height=500,
    width=800
)

### Map Visualization According to Regions

In [10]:

world_map = folium.Map(location=[11,0], tiles="cartodbpositron", zoom_start=2, max_zoom = 6, min_zoom = 2)


for i in range(0,len(confirmed_df)):
    folium.Circle(
        location=[confirmed_df.iloc[i]['Lat'], confirmed_df.iloc[i]['Long_']],
        fill=True,
        radius=int((np.log2(confirmed_df.iloc[i,-1]+1))*6000),
        color='orange',
        fill_color='#ff8533',
        tooltip = "<div style='margin: 0; background-color: black; color: white;'>"+
                    "<h4 style='text-align:center;font-weight: bold'>"+confirmed_df.index[i] + "</h4>"
                    "<hr style='margin:10px;color: white;'>"+
                    "<ul style='color: white;;list-style-type:circle;align-item:left;padding-left:20px;padding-right:20px'>"+
                        "<li>Confirmed: "+str(confirmed_df.iloc[i,-1])+"</li>"+
                        "<li>Deaths:   "+str(death_df.iloc[i,-1])+"</li>"+
                        "<li>Death Rate: "+ str(np.round(death_df.iloc[i,-1]/(confirmed_df.iloc[i,-1]+1.00001)*100,2))+ "</li>"+
                    "</ul></div>",
        ).add_to(world_map)

world_map


In [11]:
state_geo = requests.get('https://raw.githubusercontent.com/python-visualization/folium/master/examples/data/us-states.json').json()


### Map Visualization According to States - Confirmed Cases

In [12]:

data_temp = confirmed_df.groupby(["State"]).sum().reset_index().drop(["Lat","Long_"],axis=1)
data_temp["Confirmed_log"] = np.log10(data_temp.iloc[:,-1]+1)
bins = list(data_temp['Confirmed_log'].quantile([0, 0.25, 0.5, 0.75,0.95 ,1]))
m = folium.Map(location=[37, -102], zoom_start=4,max_zoom=6,min_zoom=3)
 

folium.Choropleth(
    geo_data=state_geo,
    name='choropleth',
    data = data_temp,
    columns=['State', 'Confirmed_log'],
    key_on='feature.properties.name',
    fill_color='Reds',
    fill_opacity=0.7,
    line_opacity=0.2,
    bins = bins,
    reset=True,
    legend_name='Confirmed cases log (10^x)'
).add_to(m)
folium.LayerControl().add_to(m)

legend_html = "<div style='padding:10px;background-color:rgba(255,255,255,0.5);position:fixed;bottom:20px;left:20px;z-index:1000'>"
legend_html += "<div style='width:100%;text-align:center;'><h4>Index for Legend</h4></div><hr style='border-top-color: rgba(25,25,25,0.5);'>"
legend_html += "<ul style='margin:0;padding:0;color: #555;list-style-type:circle;align-item:left;padding-left:20px;padding-right:20px'>"
for i in bins:
    legend_html += "<li style='margin:0;padding:0;line-height: 0;'>Value "+str(np.round(i,2))+" : "+str(int(10**i)-1)+"</li><br>"
legend_html += "</ul></div>"
m.get_root().html.add_child(folium.Element(legend_html))
m

### Map Visualization According to States - Death Cases

In [13]:

data_temp = death_df.groupby(["State"]).sum().reset_index().drop(["Lat","Long_"],axis=1)
data_temp["Death_log"] = np.log10(data_temp.iloc[:,-1]+1)
bins = list(data_temp['Death_log'].quantile([0, 0.25, 0.5, 0.75,0.95 ,1]))
m = folium.Map(location=[37, -102], zoom_start=4,max_zoom=6,min_zoom=3)
 

folium.Choropleth(
    geo_data=state_geo,
    name='choropleth',
    data = data_temp,
    columns=['State', 'Death_log'],
    key_on='feature.properties.name',
    fill_color='Reds',
    fill_opacity=0.7,
    line_opacity=0.2,
    bins = bins,
    reset=True,
    legend_name='Death cases log (10^x)'
).add_to(m)
folium.LayerControl().add_to(m)

legend_html = "<div style='padding:10px;background-color:rgba(255,255,255,0.5);position:fixed;bottom:20px;left:20px;z-index:1000'>"
legend_html += "<div style='width:100%;text-align:center;'><h4>Index for Legend</h4></div><hr style='border-top-color: rgba(25,25,25,0.5);'>"
legend_html += "<ul style='margin:0;padding:0;color: #555;list-style-type:circle;align-item:left;padding-left:20px;padding-right:20px'>"
for i in bins:
    legend_html += "<li style='margin:0;padding:0;line-height: 0;'>Value "+str(np.round(i,2))+" : "+str(int(10**i)-1)+"</li><br>"
legend_html += "</ul></div>"
m.get_root().html.add_child(folium.Element(legend_html))
m